# **0. Essential Packages**

In [379]:
# Clear all variables in the global namespace
globals().clear()

In [380]:
import io
import sys
import openpyxl
import random
import math

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

from matplotlib.colors import Normalize
from scipy.integrate import quad
from scipy.stats import multinomial
from scipy.stats import binom
from scipy.stats import beta
from scipy.stats import lognorm
from scipy.stats import norm
from scipy.stats import truncnorm
from scipy.stats import gaussian_kde
from scipy.special import gammaln
from ipywidgets import FileUpload

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

# **1. Import data**

In [382]:
################################################################################
#
# Data are to be imported from
# 
# https://github.com/StefanoNasini/Retrospective-Bayesian-Estimation-Pandemic-Outbreaks/tree/main/Data
#
################################################################################

# population
# M_L = ...
# M_C = ...
# M_I = ...

# daily infection and daily tests
# X_L = ...
# X_C = ...
# X_I = ...
# Z_I = ...

# covariate variables
# R_L = ...

# r_C = ...
# min_rC = np.min(r_C)
# max_rC = np.max(r_C)
# R_C = (r_C - min_rC) / (max_rC - min_rC) # min-max normalization

# time
T = list(range(32))
T1 = T[:-1]
TT = len(T1)

N1 = True

# **2. Basic Functions**

In [383]:
def F_L(lambda_h, t):
  alpha = lambda_h[0]
  qL = lambda_h[2]
  return alpha / (alpha + (1 - alpha) * np.exp(-qL * t))

#-------------------------------------------------------------------------------

def F_C(lambda_h, t):
  alpha, zeta, _, qC, _, wCL, *_ = lambda_h
  u_C_t = u_C(lambda_h, t)
  u_C_0 = u_C(lambda_h, 0)
  int_u_C_t = int_u_C(lambda_h, t)
  denominator = qC * (1 - wCL) * int_u_C_t + u_C_0 / (alpha * zeta - 1)
  if denominator == 0:
    return np.inf
  return 1 + u_C_t / denominator

def u_C(lambda_h, t):
  alpha, _, qL, qC, _, wCL, *_ = lambda_h
  r_CL = (-qC * wCL) / qL
  exp_limit = 709
  if (qL / wCL) * t >= exp_limit:
    return np.exp(-qL * (1 - wCL) * t)
  else:
    exp1 = np.exp((qL / wCL) * t)
    exp2 = np.exp(qL * ((1 - wCL) / wCL) * t)
    return (alpha * exp1 + (1 - alpha) * exp2) ** r_CL

def int_u_C(lambda_h, t):
  alpha = lambda_h[0]
  qL = lambda_h[2]
  wCL = lambda_h[5]
  if alpha > 0.0001:
    integrand = lambda x: u_C(lambda_h, x)
    h, _ = quad(integrand, 0, t)
  else:
    h = -1/(qL*(1-wCL)) * np.exp(-qL*(1-wCL)*t)
  return h
#-------------------------------------------------------------------------------

def F_I(lambda_h, t):
  qI = lambda_h[4]
  wIL = lambda_h[6]
  wIC = lambda_h[7]
  u_i_t = u_i(lambda_h, t)
  u_i_0 = u_i(lambda_h, 0)
  int_u_i_t = int_u_i(lambda_h, t)
  denominator = qI * (1 - wIL - wIC) * int_u_i_t - u_i_0
  if denominator == 0:
    return np.inf
  return 1 + u_i_t / denominator

def u_i(lambda_h, t):
  alpha, zeta, qL, qC, qI, wCL, wIL, wIC, *_ = lambda_h
  r_CL = (-qC * wCL) / qL
  r_IL = (-qI * wIL) / qL
  r_IC = (-qI * wIC) / qC
  exp_limit = 709
  if (qL / wIL) * t >= exp_limit:
    h1 = np.exp(-qI * (1 - wIL) * t)
  else:
    exp1 = np.exp((qL / wIL) * t)
    exp2 = np.exp(qL * ((1 / wIL) - 1) * t)
    h1 = (alpha * exp1 + (1 - alpha) * exp2) ** r_IL
  int_u_C_t = int_u_C(lambda_h, t)
  u_C_0 = u_C(lambda_h, 0)
  h2 = abs(qC * (1 - wCL) * int_u_C_t + u_C_0 / (alpha * zeta - 1))
  h3 = h2 ** (r_IC / (1 - wCL))
  return h1 * h3

def int_u_i(lambda_h, t):
  integrand = lambda x: u_i(lambda_h, x)
  h, _ = quad(integrand, 0, t)
  return h

In [384]:

def DeltaL_T1(lambda_h):
  tauL = lambda_h[8]
  FF_L = np.vectorize(lambda t: F_L(lambda_h, t))(T) 
  delta_L0 = np.diff(FF_L)  
  return np.power(delta_L0, 1 + tauL * R_L)  

#-------------------------------------------------------------------------------

def DeltaL_T1_a(lambda_h):
  alpha = lambda_h[0]
  q_L = lambda_h[2]
  tauL = lambda_h[8]
  exp_q_L = np.exp(q_L)
  factor_1 = (exp_q_L - 1)
  factor_2 = np.exp(q_L * (TT - 2))
  t = np.array(T1)
  g_L0 = factor_1 * ((1-t/TT) * (1 + q_L * (t-1)) + (t/TT) * factor_2 * (1+q_L*(t-TT+1)))
  delta_L0 = (alpha/(1-alpha)) * g_L0
  return np.power(delta_L0, 1 + tauL * R_L)  # Element-wise power operation

#-------------------------------------------------------------------------------

def DeltaL(lambda_h):
  alpha = lambda_h[0]
  q_L = lambda_h[2]
  F_L_0 = F_L(lambda_h, 0)
  delta_L0 = DeltaL_T1(lambda_h) if (alpha > 0.0001 or q_L > 0.01) else DeltaL_T1_a(lambda_h)
  return np.concatenate((delta_L0, [1 - np.sum(delta_L0) - F_L_0]))  

#-------------------------------------------------------------------------------

def DeltaC_T1(lambda_h):
  tauC = lambda_h[9]
  FF_C = np.vectorize(lambda t: F_C(lambda_h, t))(T)
  delta_C0 = np.diff(FF_C)
  return np.power(delta_C0, 1 - tauC * R_C)

#-------------------------------------------------------------------------------

def DeltaC(lambda_h):
  F_C_0 = F_C(lambda_h, 0)
  delta_C0 = DeltaC_T1(lambda_h)
  return np.concatenate((delta_C0, [1 - np.sum(delta_C0) - F_C_0])) 

def DeltaI_T1(lambda_h):
  FF_I = np.vectorize(lambda t: F_I(lambda_h, t))(T)
  return np.diff(FF_I)

#-------------------------------------------------------------------------------

def DeltaI(lambda_h):
  delta_I0 = DeltaI_T1(lambda_h)
  return np.concatenate((delta_I0, [1 - np.sum(delta_I0)])) 

In [385]:
def N_max(delta, N1):
  sum_delta = 0
  N_m = []
  for k in T1:
    sum_delta = sum_delta + delta[k]
    N_m.append((1 - sum_delta) / delta[k])
    N_max = np.min([1, np.min(N_m)])
    if np.isnan(N_max):
      N_max = 1

  return N_max

#-------------------------------------------------------------------------------

def DeltaT1_Theta(lambda_h):

  deltaL_T1 = DeltaL_T1(lambda_h)
  deltaC_T1 = DeltaC_T1(lambda_h)
  deltaI_T1 = DeltaI_T1(lambda_h)

  if N1:
    NL_max = N_max(deltaL_T1, N1)
    NC_max = N_max(deltaC_T1, N1)
    NI_max = N_max(deltaI_T1, N1)
  else:
    NL_max = N_max(deltaL_T1, N1) / TT
    NC_max = N_max(deltaC_T1, N1) / TT
    NI_max = N_max(deltaI_T1, N1) / TT

  thetaL = np.array([int(math.ceil(NL_max * M_L * deltaL_T1[k])) for k in T1])
  thetaC = np.array([int(math.ceil(NC_max * M_C * deltaC_T1[k])) for k in T1])
  thetaI = np.array([int(math.ceil(NI_max * M_I * deltaI_T1[k])) for k in T1])

  return {
    'thetaL': thetaL,
    'thetaC': thetaC,
    'thetaI': thetaI,
    'deltaL_T1': deltaL_T1,
    'deltaC_T1': deltaC_T1,
    'deltaI_T1': deltaI_T1
  }

In [386]:

def Pi_L(nu0, nu1, nu2, nu3):
  T1_arr = np.array(T1) + 1  
  log_power = nu3 * np.log(T1_arr)
  power = np.exp(np.clip(log_power, None, 700 * np.log(10))) 
  extra_test = np.zeros(TT)
  extra_test[23:] = nu0
  exponent = np.clip((extra_test + nu1 + nu2 * power) / M_L, -1000, 700)  
  result = 1 / (1 + np.exp(exponent))
  return np.clip(result, 1.0e-320, 0.9999999999999999)

#-------------------------------------------------------------------------------

def Pi_C(nu1, nu2, nu3):
  T1_arr = np.array(T1) + 1
  power = np.exp(np.clip(nu3 * np.log(T1_arr), None, np.log(1e308)))  # Safe power calculation
  exponent = np.clip((nu1 + nu2 * power) / M_C, -1000, 700)
  result = 1 / (1 + np.exp(exponent))
  return np.clip(result, 1.0e-320, 0.9999999999999999)

#-------------------------------------------------------------------------------

def Pi_I(nu):
  Z_I_arr = np.array(Z_I)  # Convert list to NumPy array
  exponent = np.clip((nu * Z_I_arr) / M_I, -1000, 700)
  result = 1 / (1 + np.exp(exponent))
  return np.clip(result, 1.0e-320, 0.9999999999999999)


In [387]:

def Contr_map_beta(deltaL, deltaC, deltaI, thetaL, thetaC, thetaI, betaL_mode, betaC_mode, betaI_mode, gammaL, gammaC, pi_L, pi_C, pi_I):

  # Convert lists to NumPy arrays for efficient computation
  betaL_mode = np.array(betaL_mode)
  betaC_mode = np.array(betaC_mode)
  betaI_mode = np.array(betaI_mode)

  thetaL = np.array(thetaL)
  thetaC = np.array(thetaC)
  thetaI = np.array(thetaI)

  pi_L = np.array(pi_L)
  pi_C = np.array(pi_C)
  pi_I = np.array(pi_I)

  X_L_sum = np.sum(X_L)
  X_C_sum = np.sum(X_C)
  X_I_sum = np.sum(X_I)
  gammaL_sum = np.sum(gammaL)
  gammaC_sum = np.sum(gammaC)

  f_tilde_L = pi_L / ((1 - pi_L) * deltaL[-1])
  f_tilde_C = pi_C / ((1 - pi_C) * deltaC[-1])
  f_tilde_I = pi_I / ((1 - pi_I) * deltaI[-1])

  DEN_L = f_tilde_L * (M_L - np.sum(betaL_mode) - X_L_sum - gammaL_sum)
  DEN_C = f_tilde_C * (M_C - np.sum(betaC_mode) - X_C_sum - gammaC_sum)
  DEN_I = f_tilde_I * (M_I - np.sum(betaI_mode) - X_I_sum)

  betaL = thetaL * (DEN_L / (M_L - np.sum(betaL_mode) + DEN_L))
  betaC = thetaC * (DEN_C / (M_C - np.sum(betaC_mode) + DEN_C))
  betaI = thetaI * (DEN_I / (M_I - np.sum(betaI_mode) + DEN_I))

  return {
    'betaL': betaL,
    'betaC': betaC,
    'betaI': betaI
  }


In [388]:

def Generate_Beta_Normal(thetaL, thetaC, thetaI, betaL0, betaC0, betaI0, gammaL, gammaC, ssigma_beta):

  PBL = PBC = PBI = 0  

  thetaL = np.array(thetaL)
  thetaC = np.array(thetaC)
  thetaI = np.array(thetaI)
  betaL0 = np.array(betaL0)
  betaC0 = np.array(betaC0)
  betaI0 = np.array(betaI0)

  betaC_bar = M_C - np.sum(X_C) - np.sum(gammaC)
  betaL_bar = M_L - np.sum(X_L) - np.sum(gammaL)
  betaI_bar = M_I - np.sum(X_I)

  FeasibleL = FeasibleC = FeasibleI = True

  betaL = np.zeros_like(thetaL, dtype=int)
  betaC = np.zeros_like(thetaC, dtype=int)
  betaI = np.zeros_like(thetaI, dtype=int)

  while FeasibleL or FeasibleC or FeasibleI:

    if FeasibleL:
      betaL = np.clip(np.round(np.random.normal(betaL0, ssigma_beta)), 0, thetaL).astype(int)
      PBL = np.sum(binom.logpmf(betaL[thetaL > 0], thetaL[thetaL > 0], pi_L[thetaL > 0]))
      if np.sum(betaL) <= betaL_bar:
        FeasibleL = False  

    if FeasibleC:
      betaC = np.clip(np.round(np.random.normal(betaC0, ssigma_beta)), 0, thetaC).astype(int)
      PBC = np.sum(binom.logpmf(betaC[thetaC > 0], thetaC[thetaC > 0], pi_C[thetaC > 0]))
      if np.sum(betaC) <= betaC_bar:
        FeasibleC = False  


    if FeasibleI:
      betaI = np.clip(np.round(np.random.normal(betaI0, ssigma_beta)), 0, thetaI).astype(int)
      PBI = np.sum(binom.logpmf(betaI[thetaI > 0], thetaI[thetaI > 0], pi_I[thetaI > 0]))
      if np.sum(betaI) <= betaI_bar:
        FeasibleI = False  

  return {
    'betaL': betaL.tolist(),
    'betaC': betaC.tolist(),
    'betaI': betaI.tolist(),
    'PBL': PBL,
    'PBC': PBC,
    'PBI': PBI
  }


In [389]:
################################################################################
# Auxiliary functions
################################################################################

def log_multinomial_coefficient(n, k):
  return gammaln(n + 1) - sum(gammaln(k_i + 1) for k_i in k)

# **3. Definition of Global Values**

In [390]:
class GlobalVariables:

  lambda_best = None

  betaL_best = None
  betaC_best = None
  betaI_best = None

  Nu_best = None

  gammaL_best = None
  gammaC_best = None

  Pbeta_best = None
  PS_best = None

  thetaL_best = None
  thetaC_best = None
  thetaI_best = None

  piL_best = None
  piC_best = None
  piI_best = None

  Log_Posterior_value_best = None

# **4. MLE for starting values**

## **4.1 Stage 1**

In [391]:

#------------------------
# Parameters
#------------------------
N_sim_start = 10000

GlobalVariables.Nu_best = {
  'nu0_L': 0.0,
  'nu1_L': 0.0,
  'nu2_L': 0.0,
  'nu3_L': 0.0,
  'nu1_C': 0.0,
  'nu2_C': 0.0,
  'nu3_C': 0.0,
  'nu_I': 0.0
}

GlobalVariables.Log_Posterior_value_best = float('-inf')

gammaL0 = [0] * TT
gammaC0 = [0] * TT

for sim in range(N_sim_start):

  gammaL0[0] = np.round(truncnorm.rvs((1 -50)/10 , (100 -50)/10, loc=50, scale=10, size=1))
  gammaC0[0] = np.round(truncnorm.rvs((1 -100)/50, (1000 -100)/50, loc=100, scale=50, size=1))

  for t in range(1, TT):
    gammaL0[t] = np.round(gammaL0[t-1] + truncnorm.rvs((t -50)/10 , (100 -50)/10, loc=50, scale=10, size=1))
    gammaC0[t] = np.round(gammaC0[t-1] + truncnorm.rvs((10*t -100)/50, (1000 -100)/50, loc=100, scale=50, size=1))

  gammaL0 = [arr[0] for arr in gammaL0]
  gammaC0 = [arr[0] for arr in gammaC0]

  #-------------------------------------------------------------------------------------------------------
  alpha0 = truncnorm.rvs((0.0000001-0.001)/0.001, (0.1-0.001)/0.001, loc=0.001, scale=0.001, size=1)
  zeta0 = truncnorm.rvs((0.0000001-0.1)/0.01, (0.9-0.1)/0.01, loc=0.1, scale=0.01, size=1)
  qL0 = truncnorm.rvs((0.00000001-0.003)/0.001, (1-0.003)/0.001, loc=0.003, scale=0.001, size=1)
  qC0 = truncnorm.rvs((0.00000001-0.003)/0.001, (1-0.003)/0.001, loc=0.003, scale=0.001, size=1)
  qI0 = truncnorm.rvs((0.00000001-0.05)/0.0001, (1-0.05)/0.01, loc=0.05, scale=0.01, size=1)

  wCL0 = truncnorm.rvs((0.00015-0.05)/0.01, (1-0.05)/0.01, loc=0.05, scale=0.01, size=1)
  wIL0 = truncnorm.rvs((0.00015-0.05)/0.01, (1-0.05)/0.01, loc=0.05, scale=0.01, size=1)
  wIC0 = truncnorm.rvs((0.000000001-0.05)/0.01, (1-0.05)/0.01, loc=0.05, scale=0.01, size=1)

  meanL = 0.001
  meanC = 0.001
  tauL0 = truncnorm.rvs((0.000000001-meanL)/0.01, (0.1-meanL)/0.01, loc=meanL, scale=0.01, size=1) #tauL>0
  tauC0 = truncnorm.rvs((0.000000001-meanC)/0.01, (0.1-meanC)/0.01, loc=meanC, scale=0.01, size=1) #0<tauC<1

  lambda_0 = [alpha0[0], zeta0[0], qL0[0], qC0[0], qI0[0], wCL0[0], wIL0[0], wIC0[0], tauL0[0], tauC0[0]]

  deltaC = DeltaC(lambda_0) ##
  deltaI = DeltaI(lambda_0) ##

  if (wIL0 + wIC0 >= 1) or np.any(deltaC<=0) or np.any(deltaI<=0):
    continue

  deltaL = DeltaL(lambda_0) ##

  DeltaT1_Theta_dictionary = DeltaT1_Theta(lambda_0) ##
  thetaL = DeltaT1_Theta_dictionary['thetaL']
  thetaC = DeltaT1_Theta_dictionary['thetaC']
  thetaI = DeltaT1_Theta_dictionary['thetaI']

  #------------------------------------------------------------------------------------------------------------------------------
  nu0_L = truncnorm.rvs((0.00-10)/1, (100-10)/1, loc=10, scale=1, size=1)
  nu1_L = np.random.normal(GlobalVariables.Nu_best['nu1_L'], (100/(1+sim)) + np.sqrt(abs(GlobalVariables.Nu_best['nu1_L'])))
  nu2_L = np.random.normal(GlobalVariables.Nu_best['nu2_L'], (100/(1+sim)) + np.sqrt(abs(GlobalVariables.Nu_best['nu2_L'])))
  nu3_L = np.random.normal(GlobalVariables.Nu_best['nu3_L'], (100/(1+sim)) + np.sqrt(abs(GlobalVariables.Nu_best['nu3_L'])))

  nu1_C = np.random.normal(GlobalVariables.Nu_best['nu1_C'], (100/(1+sim)) + np.sqrt(abs(GlobalVariables.Nu_best['nu1_C'])))
  nu2_C = np.random.normal(GlobalVariables.Nu_best['nu2_C'], (100/(1+sim)) + np.sqrt(abs(GlobalVariables.Nu_best['nu2_C'])))
  nu3_C = np.random.normal(GlobalVariables.Nu_best['nu3_C'], (100/(1+sim)) + np.sqrt(abs(GlobalVariables.Nu_best['nu3_C'])))

  nu_I = np.random.normal(GlobalVariables.Nu_best['nu_I'], (100/(1+sim)) + np.sqrt(abs(GlobalVariables.Nu_best['nu_I'])))

  Nu = {
    'nu0_L': nu0_L,
    'nu1_L': nu1_L,
    'nu2_L': nu2_L,
    'nu3_L': nu3_L,
    'nu1_C': nu1_C,
    'nu2_C': nu2_C,
    'nu3_C': nu3_C,
    'nu_I': nu_I
    }

  pi_L = Pi_L(nu0_L, nu1_L, nu2_L, nu3_L)
  pi_C = Pi_C(nu1_C, nu2_C, nu3_C)
  pi_I = Pi_I(nu_I)

  #-----------------------------------------------------------------------

  betaL_mode = [np.floor((thetaL[k]+1) * pi_L[k]) for k in T1]
  betaC_mode = [np.floor((thetaC[k]+1) * pi_C[k]) for k in T1]
  betaI_mode = [np.floor((thetaI[k]+1) * pi_I[k]) for k in T1]

  GAP = M_L
  betaL0 = betaL_mode.copy()
  CM_iter = 0
  while (GAP > 0.0001) & (CM_iter < 100):
    beta_updated = Contr_map_beta(deltaL, deltaC, deltaI, thetaL, thetaC, thetaI, betaL_mode, betaC_mode, betaI_mode, gammaL0, gammaC0, pi_L, pi_C, pi_I) ##
    betaL_updated = beta_updated['betaL']
    betaC_updated = beta_updated['betaC']
    betaI_updated = beta_updated['betaI']
    GAP = (np.abs(np.sum(betaL0) - np.sum(betaL_updated)))/( 1 + max([np.sum(betaL0), np.sum(betaL_updated)]))
    betaL0 = betaL_updated
    betaL_mode = betaL_updated
    betaC_mode = betaC_updated
    betaI_mode = betaI_updated
    CM_iter = CM_iter + 1

  betaL = [math.ceil(x) for x in beta_updated['betaL']]
  betaC = [math.ceil(x) for x in beta_updated['betaC']]
  betaI = [math.ceil(x) for x in beta_updated['betaI']]

  PBL = 0
  PBC = 0
  PBI = 0
  for k in T1:
    PBL += binom.logpmf(betaL[k], thetaL[k], pi_L[k])
    PBC += binom.logpmf(betaC[k], thetaC[k], pi_C[k])
    PBI += binom.logpmf(betaI[k], thetaI[k], pi_I[k])
  Pbeta = PBL + PBC + PBI

  #-----------------------------------------------------------------------
  S_L_T1 = [X_L[k] + gammaL0[k] for k in T1]
  S_C_T1 = [X_C[k] + gammaC0[k] for k in T1]

  S_L = np.append(S_L_T1, M_L - np.sum(S_L_T1) - np.sum(betaL))
  S_C = np.append(S_C_T1, M_C - np.sum(S_C_T1) - np.sum(betaC))
  S_I = np.append(X_I, M_I - np.sum(X_I) - np.sum(betaI))

  Ps_L = sum(np.log(deltaL)*S_L) + log_multinomial_coefficient(M_L - np.sum(betaL), S_L)
  Ps_C = sum(np.log(deltaC)*S_C) + log_multinomial_coefficient(M_C - np.sum(betaC), S_C)
  Ps_I = sum(np.log(deltaI)*S_I) + log_multinomial_coefficient(M_I - np.sum(betaI), S_I)
  PS = Ps_L + Ps_C + Ps_I

  Log_Posterior_value_new = Pbeta + PS

  if Log_Posterior_value_new > GlobalVariables.Log_Posterior_value_best:

    GlobalVariables.lambda_best = lambda_0.copy()

    GlobalVariables.betaL_best = betaL.copy()
    GlobalVariables.betaC_best = betaC.copy()
    GlobalVariables.betaI_best = betaI.copy()

    GlobalVariables.Nu_best = Nu.copy()

    GlobalVariables.gammaL_best = gammaL0.copy()  # or GlobalVariables.gammaL_best = gammaL0[:]
    GlobalVariables.gammaC_best = gammaC0.copy()  # or GlobalVariables.gammaL_best = gammaC0[:]

    GlobalVariables.Pbeta_best = Pbeta
    GlobalVariables.PS_best = PS

    GlobalVariables.thetaL_best = thetaL.copy()
    GlobalVariables.thetaC_best = thetaC.copy()
    GlobalVariables.thetaI_best = thetaI.copy()

    GlobalVariables.piL_best = pi_L.copy()
    GlobalVariables.piC_best = pi_C.copy()

    GlobalVariables.piI_best = pi_I.copy()

    GlobalVariables.Log_Posterior_value_best = Log_Posterior_value_new

  print('Simul=', sim, 'CM-iter=', CM_iter, 'Updated posterior probability:', GlobalVariables.Log_Posterior_value_best)


Simul= 0 CM-iter= 2 Updated posterior probability: -1269427.4996252162
Simul= 1 CM-iter= 2 Updated posterior probability: -1269427.4996252162
Simul= 2 CM-iter= 2 Updated posterior probability: -1269427.4996252162
Simul= 3 CM-iter= 2 Updated posterior probability: -1117668.6214054993
Simul= 4 CM-iter= 2 Updated posterior probability: -1117668.6214054993
Simul= 5 CM-iter= 2 Updated posterior probability: -670028.3515049634
Simul= 6 CM-iter= 2 Updated posterior probability: -670028.3515049634
Simul= 7 CM-iter= 2 Updated posterior probability: -670028.3515049634
Simul= 8 CM-iter= 2 Updated posterior probability: -670028.3515049634
Simul= 9 CM-iter= 2 Updated posterior probability: -670028.3515049634
Simul= 10 CM-iter= 2 Updated posterior probability: -535737.2815312945
Simul= 11 CM-iter= 2 Updated posterior probability: -535737.2815312945
Simul= 12 CM-iter= 1 Updated posterior probability: -535737.2815312945
Simul= 13 CM-iter= 2 Updated posterior probability: -535737.2815312945
Simul= 14 C

## **4.2 Stage 2**

In [392]:

#------------------------
# Parameters
#------------------------

N_sim_start = 1000

gammaL0 = [0] * TT
gammaC0 = [0] * TT

for sim in range(N_sim_start):

  convex_comb =  np.sqrt((N_sim_start+sim)/(1 + 2*N_sim_start))

  gammaL0[0] = np.round(truncnorm.rvs((1 -50)/10 , (100 -50)/10, loc=50, scale=10, size=1))
  gammaC0[0] = np.round(truncnorm.rvs((1 -100)/50, (1000 -100)/50, loc=100, scale=50, size=1))

  for t in range(1, TT):
    gammaL0[t] = np.round(gammaL0[t-1] + truncnorm.rvs((t -50)/10 , (100 -50)/10, loc=50, scale=10, size=1))
    gammaC0[t] = np.round(gammaC0[t-1] + truncnorm.rvs((10*t -100)/50, (1000 -100)/50, loc=100, scale=50, size=1))

  gammaL = np.round([convex_comb * GlobalVariables.gammaL_best[t] + (1-convex_comb) * gammaL0[t] for t in range(TT)])
  gammaC = np.round([convex_comb * GlobalVariables.gammaC_best[t] + (1-convex_comb) * gammaC0[t] for t in range(TT)])

  gammaL0 = [arr[0] for arr in gammaL]
  gammaC0 = [arr[0] for arr in gammaC]

  #-------------------------------------------------------------------------------------------------------
  alpha0 = truncnorm.rvs((0.0000001-0.001)/0.001, (0.1-0.001)/0.001, loc=0.001, scale=0.001, size=1)
  zeta0 = truncnorm.rvs((0.0000001-0.1)/0.01, (0.9-0.1)/0.01, loc=0.1, scale=0.01, size=1)
  qL0 = truncnorm.rvs((0.000000001-0.003)/0.001, (1-0.003)/0.001, loc=0.003, scale=0.001, size=1)
  qC0 = truncnorm.rvs((0.000000001-0.003)/0.001, (1-0.003)/0.001, loc=0.003, scale=0.001, size=1)
  qI0 = truncnorm.rvs((0.000000001-0.05)/0.0001, (1-0.05)/0.01, loc=0.05, scale=0.01, size=1)

  wCL0 = truncnorm.rvs((0.00015-0.05)/0.01, (1-0.05)/0.01, loc=0.05, scale=0.01, size=1)
  wIL0 = truncnorm.rvs((0.00015-0.05)/0.01, (1-0.05)/0.01, loc=0.05, scale=0.01, size=1)
  wIC0 = truncnorm.rvs((0.000000001-0.05)/0.01, (1-0.05)/0.01, loc=0.05, scale=0.01, size=1)

  meanL = 0.001
  meanC = 0.001
  tauL0 = truncnorm.rvs((0.000000001-meanL)/0.01, (0.1-meanL)/0.01, loc=meanL, scale=0.01, size=1) #tauL>0
  tauC0 = truncnorm.rvs((0.000000001-meanC)/0.01, (0.1-meanC)/0.01, loc=meanC, scale=0.01, size=1) #0<tauC<1

  alpha0 = convex_comb*GlobalVariables.lambda_best[0] + (1-convex_comb)*alpha0
  zeta0 = convex_comb*GlobalVariables.lambda_best[1] + (1-convex_comb)*zeta0
  qL0 = convex_comb*GlobalVariables.lambda_best[2] + (1-convex_comb)*qL0
  qC0 = convex_comb*GlobalVariables.lambda_best[3] + (1-convex_comb)*qC0
  qI0 = convex_comb*GlobalVariables.lambda_best[4] + (1-convex_comb)*qI0
  wCL0 = convex_comb*GlobalVariables.lambda_best[5] + (1-convex_comb)*wCL0
  wIL0 = convex_comb*GlobalVariables.lambda_best[6] + (1-convex_comb)*wIL0
  wIC0 = convex_comb*GlobalVariables.lambda_best[7] + (1-convex_comb)*wIC0
  tauL0 = convex_comb*GlobalVariables.lambda_best[8] + (1-convex_comb)*tauL0
  tauC0 = convex_comb*GlobalVariables.lambda_best[9] + (1-convex_comb)*tauC0

  lambda_0 = [alpha0[0], zeta0[0], qL0[0], qC0[0], qI0[0], wCL0[0], wIL0[0], wIC0[0], tauL0[0], tauC0[0]]

  deltaC = DeltaC(lambda_0) ##
  deltaI = DeltaI(lambda_0) ##

  if (wIL0 + wIC0 >= 1) or np.any(deltaC<=0) or np.any(deltaI<=0):
      continue

  deltaL = DeltaL(lambda_0) ##

  DeltaT1_Theta_dictionary = DeltaT1_Theta(lambda_0) ##
  thetaL = DeltaT1_Theta_dictionary['thetaL']
  thetaC = DeltaT1_Theta_dictionary['thetaC']
  thetaI = DeltaT1_Theta_dictionary['thetaI']

  #-------------------------------------------------------------------------------------------------------------------
  nu0_L = nu0_L = truncnorm.rvs((0.00-1)/1, (10-1)/1, loc=1, scale=1, size=1)
  nu1_L = np.random.normal(GlobalVariables.Nu_best['nu1_L'], (1-convex_comb)*abs(GlobalVariables.Nu_best['nu1_L']))
  nu2_L = np.random.normal(GlobalVariables.Nu_best['nu2_L'], (1-convex_comb)*abs(GlobalVariables.Nu_best['nu2_L']))
  nu3_L = np.random.normal(GlobalVariables.Nu_best['nu3_L'], (1-convex_comb)*abs(GlobalVariables.Nu_best['nu3_L']))

  nu1_C = np.random.normal(GlobalVariables.Nu_best['nu1_C'], (1-convex_comb)*abs(GlobalVariables.Nu_best['nu1_C']))
  nu2_C = np.random.normal(GlobalVariables.Nu_best['nu2_C'], (1-convex_comb)*abs(GlobalVariables.Nu_best['nu2_C']))
  nu3_C = np.random.normal(GlobalVariables.Nu_best['nu3_C'], (1-convex_comb)*abs(GlobalVariables.Nu_best['nu3_C']))

  nu_I = np.random.normal(GlobalVariables.Nu_best['nu_I'], (1-convex_comb)*abs(GlobalVariables.Nu_best['nu_I']))

  Nu = {
    'nu0_L': nu0_L,
    'nu1_L': nu1_L,
    'nu2_L': nu2_L,
    'nu3_L': nu3_L,
    'nu1_C': nu1_C,
    'nu2_C': nu2_C,
    'nu3_C': nu3_C,
    'nu_I': nu_I
  }

  pi_L = Pi_L(nu0_L, nu1_L, nu2_L, nu3_L)
  pi_C = Pi_C(nu1_C, nu2_C, nu3_C)
  pi_I = Pi_I(nu_I)

  #-----------------------------------------------------------------------
  # Create a starting beta using Proposition 4
  betaL_mode = [np.floor((thetaL[k]+1) * pi_L[k]) for k in T1]
  betaC_mode = [np.floor((thetaC[k]+1) * pi_C[k]) for k in T1]
  betaI_mode = [np.floor((thetaI[k]+1) * pi_I[k]) for k in T1]

  GAP = M_L
  betaL0 = betaL_mode.copy()
  CM_iter = 0
  while (GAP > 0.0001) & (CM_iter < 100):
    beta_updated = Contr_map_beta(deltaL, deltaC, deltaI, thetaL, thetaC, thetaI, betaL_mode, betaC_mode, betaI_mode, gammaL0, gammaC0, pi_L, pi_C, pi_I) ##
    betaL_updated = beta_updated['betaL']
    betaC_updated = beta_updated['betaC']
    betaI_updated = beta_updated['betaI']
    GAP = (np.abs(np.sum(betaL0) - np.sum(betaL_updated)))/(1 + max([np.sum(betaL0), np.sum(betaL_updated)]))
    betaL_mode = betaL_updated
    betaC_mode = betaC_updated
    betaI_mode = betaI_updated
    betaL0 = betaL_updated
    CM_iter = CM_iter + 1

  betaL = [math.ceil(x) for x in beta_updated['betaL']]
  betaC = [math.ceil(x) for x in beta_updated['betaC']]
  betaI = [math.ceil(x) for x in beta_updated['betaI']]

  PBL = 0
  PBC = 0
  PBI = 0
  for k in T1:
    PBL += binom.logpmf(betaL[k], thetaL[k], pi_L[k])
    PBC += binom.logpmf(betaC[k], thetaC[k], pi_C[k])
    PBI += binom.logpmf(betaI[k], thetaI[k], pi_I[k])

  Pbeta = PBL + PBC + PBI

  #-----------------------------------------------------------------------
  S_L_T1 = [X_L[k] + gammaL[k] for k in T1]
  S_C_T1 = [X_C[k] + gammaC[k] for k in T1]

  S_L = np.append(S_L_T1, M_L - np.sum(S_L_T1) - np.sum(betaL))
  S_C = np.append(S_C_T1, M_C - np.sum(S_C_T1) - np.sum(betaC))
  S_I = np.append(X_I, M_I - np.sum(X_I) - np.sum(betaI))

  Ps_L = sum(np.log(deltaL)*S_L) + log_multinomial_coefficient(M_L - np.sum(betaL), S_L)
  Ps_C = sum(np.log(deltaC)*S_C) + log_multinomial_coefficient(M_C - np.sum(betaC), S_C)
  Ps_I = sum(np.log(deltaI)*S_I) + log_multinomial_coefficient(M_I - np.sum(betaI), S_I)

  PS = Ps_L + Ps_C + Ps_I

  #-----------------------------------------------------------------------
  Log_Posterior_value_new = Pbeta + PS

  if Log_Posterior_value_new > GlobalVariables.Log_Posterior_value_best:

    GlobalVariables.lambda_best = lambda_0.copy()

    GlobalVariables.betaL_best = betaL.copy()
    GlobalVariables.betaC_best = betaC.copy()
    GlobalVariables.betaI_best = betaI.copy()

    GlobalVariables.gammaL_best = gammaL0.copy()  # or GlobalVariables.gammaL_best = gammaL0[:]
    GlobalVariables.gammaC_best = gammaC0.copy()  # or GlobalVariables.gammaL_best = gammaC0[:]

    GlobalVariables.Pbeta_best = Pbeta
    GlobalVariables.PS_best = PS

    GlobalVariables.thetaL_best = thetaL.copy()
    GlobalVariables.thetaC_best = thetaC.copy()
    GlobalVariables.thetaI_best = thetaI.copy()

    GlobalVariables.piL_best = pi_L.copy()
    GlobalVariables.piC_best = pi_C.copy()
    GlobalVariables.piI_best = pi_I.copy()

    GlobalVariables.Log_Posterior_value_best = Log_Posterior_value_new

  print('Simul=', sim, 'CM-iter=', CM_iter, 'Candidate posterior probability:', Log_Posterior_value_new ,'Updated posterior probability:', GlobalVariables.Log_Posterior_value_best)


Simul= 0 CM-iter= 2 Candidate posterior probability: -410152.16452888795 Updated posterior probability: -274566.33718793886
Simul= 1 CM-iter= 2 Candidate posterior probability: -454840.9913641973 Updated posterior probability: -274566.33718793886
Simul= 2 CM-iter= 2 Candidate posterior probability: -445609.91398070526 Updated posterior probability: -274566.33718793886
Simul= 3 CM-iter= 2 Candidate posterior probability: -388251.3522378503 Updated posterior probability: -274566.33718793886
Simul= 4 CM-iter= 2 Candidate posterior probability: -436630.7332776042 Updated posterior probability: -274566.33718793886
Simul= 5 CM-iter= 2 Candidate posterior probability: -347079.37910868553 Updated posterior probability: -274566.33718793886
Simul= 6 CM-iter= 2 Candidate posterior probability: -347711.8455002881 Updated posterior probability: -274566.33718793886
Simul= 7 CM-iter= 2 Candidate posterior probability: -583613.3215931624 Updated posterior probability: -274566.33718793886
Simul= 8 CM-i

# **5. Estimation**

In [393]:
################################################################################
# Main loop 
################################################################################

pi_L = GlobalVariables.piL_best
pi_C = GlobalVariables.piC_best
pi_I = GlobalVariables.piI_best

#-------------------------------------------------------------------------------
a = 0.5
b = 2000 # The variance of the candidate is decreasing in b
sigma = 1.0e-9
sigma_beta = 0.4

acceptG = 0
total_iter = 1

# Scale of iteration

E_iter = 500

Total_alpha = []
Total_zeta = []
Total_qL = []
Total_qC = []
Total_qI = []
Total_wCL = []
Total_wIL = []
Total_wIC = []
Total_tauL = []
Total_tauC = []

#-------------------------------------------------------------------------------
gammaL_old = GlobalVariables.gammaL_best
gammaC_old = GlobalVariables.gammaC_best

lambda_old = GlobalVariables.lambda_best

alpha_old = GlobalVariables.lambda_best[0]
zeta_old = GlobalVariables.lambda_best[1]
qL_old = GlobalVariables.lambda_best[2]
qC_old = GlobalVariables.lambda_best[3]
qI_old = GlobalVariables.lambda_best[4]
wCL_old = GlobalVariables.lambda_best[5]
wIL_old = GlobalVariables.lambda_best[6]
wIC_old = GlobalVariables.lambda_best[7]
tauL_old = GlobalVariables.lambda_best[8]
tauC_old = GlobalVariables.lambda_best[9]

P_Sbeta_old = GlobalVariables.Log_Posterior_value_best

ThetaPiL_old = np.array(GlobalVariables.thetaL_best) * pi_L
ThetaPiC_old = np.array(GlobalVariables.thetaC_best) * pi_C
ThetaPiI_old = np.array(GlobalVariables.thetaI_best) * pi_I

betaL_old = GlobalVariables.betaL_best
betaC_old = GlobalVariables.betaC_best
betaI_old = GlobalVariables.betaI_best

#-------------------------------------------------------------------------------
for e_iter in range(E_iter):

  sigma = max(1.0e-11, sigma/np.sqrt((1+1/(e_iter+10))))
  sigma_beta = max(0.15, sigma_beta/np.sqrt((1+1/(e_iter+10))))

  print('E-step', e_iter)

  ############################################################################

  samples_alpha = []
  samples_zeta = []
  samples_qL = []
  samples_qC = []
  samples_qI = []
  samples_wCL = []
  samples_wIL = []
  samples_wIC = []
  samples_tauL = []
  samples_tauC = []
  samples_ThetaPiL = []
  samples_ThetaPiC = []

  MH_iter = round(100 + (2000)/(1+e_iter))

  for mh_iter in range(MH_iter):

    print('MH-step', mh_iter)

    #-----------------------------------------------------------------------

    infeasible = True

    while infeasible:

      alpha_new = np.random.normal(alpha_old, sigma)
      zeta_new = np.random.normal(zeta_old, 10*sigma)
      qL_new = np.random.normal(qL_old, 1000*sigma)
      qC_new = np.random.normal(qC_old, 1000*sigma)
      qI_new = np.random.normal(qI_old, 1000*sigma)
      wCL_new = np.random.normal(wCL_old, 10*sigma)
      wIC_new = np.random.normal(wIC_old, 10*sigma)
      wIL_new = np.random.normal(wIL_old, 10*sigma)
      tauL_new = np.random.normal(tauL_old, 10*sigma)
      tauC_new = np.random.normal(tauC_old, 10*sigma)

      lambda_new = [alpha_new, zeta_new, qL_new, qC_new, qI_new, wCL_new, wIL_new, wIC_new, tauL_new, tauC_new]

      deltaL = DeltaL(lambda_new) ##
      deltaC = DeltaC(lambda_new) ##
      deltaI = DeltaI(lambda_new) ##

      Condition1 = (alpha_new < 1) and (alpha_new > 0) and (zeta_new < 1) and (zeta_new > 0)
      Condition2 = (wCL_new < 1) and (wCL_new > 0) and (wIC_new < 1) and (wIC_new > 0) and (wIL_new < 1) and (wIL_new > 0)
      Condition3 = (qL_new > 0) and (qC_new > 0) and (qI_new > 0)
      Condition4 = (wIC_new + wIL_new<=1) and np.all(deltaL>0) and np.all(deltaC>0) and np.all(deltaI>0)

      if (Condition1 and Condition2 and Condition3 and Condition4):
        infeasible = False

    #-----------------------------------------------------------------------
    DeltaT1_Theta_dictionary = DeltaT1_Theta(lambda_new)

    thetaL = DeltaT1_Theta_dictionary['thetaL']
    thetaC = DeltaT1_Theta_dictionary['thetaC']
    thetaI = DeltaT1_Theta_dictionary['thetaI']

    deltaL_T1 = DeltaT1_Theta_dictionary['deltaL_T1']
    deltaC_T1 = DeltaT1_Theta_dictionary['deltaC_T1']
    deltaI_T1 = DeltaT1_Theta_dictionary['deltaI_T1']

    #-----------------------------------------------------------------------
    ThetaPiL_new = np.array(thetaL) * pi_L
    ThetaPiC_new = np.array(thetaC) * pi_C
    samples_ThetaPiL.append(np.sum(ThetaPiL_new)) #
    samples_ThetaPiC.append(np.sum(ThetaPiC_new)) #

    #-----------------------------------------------------------------------
    # Generate new beta
    #-----------------------------------------------------------------------

    Beta_object = Generate_Beta_Normal(thetaL, thetaC, thetaI, betaL_old, betaC_old, betaI_old, gammaL_old, gammaC_old, sigma_beta)

    betaL_new = Beta_object['betaL']
    betaC_new = Beta_object['betaC']
    betaI_new = Beta_object['betaI']

    PBL = Beta_object['PBL']
    PBC = Beta_object['PBC']
    PBI = Beta_object['PBI']

    Pbeta_new = PBL + PBC + PBI

    #-----------------------------------------------------------------------
    S_L_T1 = [X_L[k] + gammaL_old[k] for k in T1]
    S_C_T1 = [X_C[k] + gammaC_old[k] for k in T1]

    S_L_new = np.append(S_L_T1, M_L - np.sum(S_L_T1) - np.sum(betaL_new))
    S_C_new = np.append(S_C_T1, M_C - np.sum(S_C_T1) - np.sum(betaC_new))
    S_I_new = np.append(X_I, M_I - np.sum(X_I) - np.sum(betaI_new))

    Ps_L_new = sum(np.log(deltaL)*S_L_new) + log_multinomial_coefficient(M_L-np.sum(betaL_new), S_L_new)
    Ps_C_new = sum(np.log(deltaC)*S_C_new) + log_multinomial_coefficient(M_C-np.sum(betaC_new), S_C_new)
    Ps_I_new = sum(np.log(deltaI)*S_I_new) + log_multinomial_coefficient(M_I-np.sum(betaI_new), S_I_new)

    PS_new = Ps_L_new + Ps_C_new + Ps_I_new

    #---------------------------------------------------------------

    P_Sbeta_new = Pbeta_new + PS_new

    accept_prob = np.exp(min(700, P_Sbeta_new - P_Sbeta_old ))

    print(P_Sbeta_old)

    if np.random.uniform(0, 1) < accept_prob:

      acceptG = acceptG + 1

      print('ACCEPTED: MH-step iteration = ', mh_iter, 'Total iterations = ', total_iter, ' acceptance prob = ', accept_prob)

      alpha_old = alpha_new
      zeta_old = zeta_new
      qL_old = qL_new
      qC_old = qC_new
      qI_old = qI_new
      wCL_old = wCL_new
      wIL_old = wIL_new
      wIC_old = wIC_new
      tauL_old = tauL_new
      tauC_old = tauC_new

      betaL_old = betaL_new.copy()
      betaC_old = betaC_new.copy()
      betaI_old = betaI_new.copy()

      lambda_old = lambda_new.copy()

      P_Sbeta_old = P_Sbeta_new
      GlobalVariables.Log_Posterior_value_best = P_Sbeta_old

    else:
      print('REJECTED: MH-step iteration = ', mh_iter, 'Total iterations = ', total_iter, ' acceptance prob = ', accept_prob)

    print('Acceptance rate:', (acceptG/total_iter))

    samples_alpha.append(alpha_old) #
    samples_zeta.append(zeta_old) #
    samples_qL.append(qL_old) #
    samples_qC.append(qC_old) #
    samples_qI.append(qI_old) #
    samples_wCL.append(wCL_old) #
    samples_wIL.append(wIL_old) #
    samples_wIC.append(wIC_old) #
    samples_tauL.append(tauL_old) #
    samples_tauC.append(tauC_old) #

    total_iter = total_iter + 1

  ############################################################################

  burn_in = int(MH_iter * 0.1)
  rest = MH_iter - burn_in

  samples_alpha = np.array(samples_alpha[burn_in:])
  samples_zeta = np.array(samples_zeta[burn_in:])
  samples_qL = np.array(samples_qL[burn_in:])
  samples_qC = np.array(samples_qC[burn_in:])
  samples_qI = np.array(samples_qI[burn_in:])
  samples_wCL = np.array(samples_wCL[burn_in:])
  samples_wIL = np.array(samples_wIL[burn_in:])
  samples_wIC = np.array(samples_wIC[burn_in:])
  samples_tauL = np.array(samples_tauL[burn_in:])
  samples_tauC = np.array(samples_tauC[burn_in:])
  samples_ThetaPiL = np.array(samples_ThetaPiL[burn_in:])
  samples_ThetaPiC = np.array(samples_ThetaPiC[burn_in:])

  alpha_e = np.mean(samples_alpha)
  zeta_e = np.mean(samples_zeta)
  qL_e = np.mean(samples_qL)
  qC_e = np.mean(samples_qC)
  qI_e = np.mean(samples_qI)
  wCL_e = np.mean(samples_wCL)
  wIL_e = np.mean(samples_wIL)
  wIC_e = np.mean(samples_wIC)
  tauL_e = np.mean(samples_tauL)
  tauC_e = np.mean(samples_tauC)

  Total_alpha.extend(samples_alpha)
  Total_zeta.extend(samples_zeta)
  Total_qL.extend(samples_qL)
  Total_qC.extend(samples_qC)
  Total_qI.extend(samples_qI)
  Total_wCL.extend(samples_wCL)
  Total_wIL.extend(samples_wIL)
  Total_wIC.extend(samples_wIC)
  Total_tauL.extend(samples_tauL)
  Total_tauC.extend(samples_tauC)

  ############################################################################

  lambda_E = [alpha_e, zeta_e, qL_e, qC_e, qI_e, wCL_e, wIL_e, wIC_e, tauL_e, tauC_e]
  deltaL_E = DeltaL(lambda_E) ##
  deltaC_E = DeltaC(lambda_E) ##

  ThetaPi_L = np.mean(samples_ThetaPiL)
  ThetaPi_C = np.mean(samples_ThetaPiC)

  gammaL_new = []
  gammaC_new = []
  for k in T1:
    eL1 = (M_L - ThetaPi_L) * deltaL_E[k] - X_L[k]
    comb_eL = np.ceil(a * gammaL_old[k] + (1-a) * eL1)
    eL = np.max([0.0, comb_eL])
    gammaL_new.append(eL)
    eC1 = (M_C - ThetaPi_C) * deltaC_E[k] - X_C[k]
    comb_eC = np.ceil(a * gammaC_old[k] + (1-a) * eC1)
    eC = np.max([0.0, comb_eC])
    gammaC_new.append(eC)

  gammaL_old = gammaL_new.copy()
  gammaC_old = gammaC_new.copy()

E-step 0
MH-step 0
-274566.33718793886
REJECTED: MH-step iteration =  0 Total iterations =  1  acceptance prob =  0.0
Acceptance rate: 0.0
MH-step 1
-274566.33718793886
ACCEPTED: MH-step iteration =  1 Total iterations =  2  acceptance prob =  1.0142320547350045e+304
Acceptance rate: 0.5
MH-step 2
-273353.4963206087
ACCEPTED: MH-step iteration =  2 Total iterations =  3  acceptance prob =  1.0142320547350045e+304
Acceptance rate: 0.6666666666666666
MH-step 3
-272191.6563527294
ACCEPTED: MH-step iteration =  3 Total iterations =  4  acceptance prob =  2.838305505253189e+27
Acceptance rate: 0.75
MH-step 4
-272128.44334799756
REJECTED: MH-step iteration =  4 Total iterations =  5  acceptance prob =  0.0
Acceptance rate: 0.6
MH-step 5
-272128.44334799756
ACCEPTED: MH-step iteration =  5 Total iterations =  6  acceptance prob =  123307.26232093142
Acceptance rate: 0.6666666666666666
MH-step 6
-272116.72091341054
REJECTED: MH-step iteration =  6 Total iterations =  7  acceptance prob =  8.37